In [1]:
import pandas as pd
import numpy as np

In [2]:
dy4 = pd.read_csv('C:/Master/yellow_tripdata_2015-04_2.csv')

# Visualizamos

In [3]:
import datashader as ds
from datashader import transfer_functions as tr_fns
from datashader.colors import Greys9
Greys9_r = list(reversed(Greys9))[:2]

In [4]:
from bokeh.plotting import figure, output_notebook, show
output_notebook()

Loading BokehJS ...

In [5]:
NYC = x_range, y_range = ((-75.00, -73.0), (40.0, 41.0))

plot_width = int(750)
plot_height = int(plot_width//1.2)

In [6]:
def base_plot(tools='pan, wheel_zoom, reset', plot_width=plot_width, plot_height=plot_height, **plot_args):
    p = figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
              x_range=x_range, y_range=y_range, outline_line_color=None,
              min_border=0, min_border_left=0, min_border_right=0,
              min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    return p

In [7]:
ejemplo = dy4.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='blue', size=5)

p.circle(x=ejemplo['pickup_longitude'], y=ejemplo['pickup_latitude'], **options)
show(p)

In [8]:
ejemplo = dy4.sample(n=15000)
p = base_plot()
options = dict(line_color=None, fill_color='red', size=5)

p.circle(x=ejemplo['dropoff_longitude'], y=ejemplo['dropoff_latitude'], **options)
show(p)

# Visualización con HeatMap

In [9]:
from datashader.bokeh_ext import InteractiveImage
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno
from IPython.core.display import HTML, display

background = "black"
export = partial(export_image, export_path="export", background=background)
cm = partial(colormap_select, reverse=(background=="black"))

In [10]:
def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(dy4, 'dropoff_longitude', 'dropoff_latitude', ds.count('passenger_count'))
    img = tr_fns.shade(agg, cmap=Hot, how='eq_hist')
    return tr_fns.dynspread(img, threshold=0.5, max_px=4)

p = base_plot(background_fill_color=background)
export(create_image(*NYC), "NYCABs")
InteractiveImage(p, create_image)

In [11]:
def create_image(x_range, y_range, w=plot_width, h=plot_height):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(dy4, 'pickup_longitude', 'pickup_latitude', ds.count('passenger_count'))
    img = tr_fns.shade(agg, cmap=Hot, how='eq_hist')
    return tr_fns.dynspread(img, threshold=0.5, max_px=4)

p = base_plot(background_fill_color=background)
export(create_image(*NYC), "NYCABs_Recoger")
InteractiveImage(p, create_image)

Indicar que no vemos diferencias entre meses 03 y 04, observamos que hay diferencias entre zonas de recogida y dejar pasaje, este tipo de taxis, tiene como preferencia la zona del bajo Manhattan.

Observamos que la zona de recogida preferida son los barrios del bajo Manhattan, con una fuerte presencia.

Observamos que este tipo de taxis recoge pasaje en los aeropuertos, tanto JFK, la Guardia y New Yersey. Siendo especialmente fuerte la recogida en JFK y La Guardia, menor en New Jersey.

Dejar pasaje, es fuerte la presencia en los tres aeropuertos, la zona de bajo Manhattan tiene mucho servicios a estos.

Hemos observado que usando la libreria datashader se realiza una buena visualización de mapa de calor, realizando una cartografia muy buena del terreno, con fuerte luz en las zonas de mas influencia, es una buena libreria a tener presente para datos con coordenadas de geolocalización.